# process the pdfs 
### Connect to mongodb and make sure we have access to the pdf files

In [2]:
from pymongo import MongoClient
from gridfs import GridFSBucket
import pandas as pd

# Connect to MongoDB
db = MongoClient('mongodb://192.168.1.10:27017')['supercias']

# get files from GridFS 'companies.files'
bucket = GridFSBucket(db, bucket_name='companies')

# find one pdf to make sure it works
file = bucket.find().limit(1).next()
print(file.filename)

1790016919001_DocumentosGenerales_Oficio Transferencia Acciones_1989-02-13.pdf


#### Check the integrity of the pdfs

delete all file that are too small to be valis pdfs

In [3]:
query = { 'length': { '$lt': 69 } }
count = bucket.find(query).collection.count_documents(query)
print('documents found:', count)
cursor = bucket.find(query)
for file in cursor:
    # set a delete file 
    print(file.length, '-->', file.filename)
    db['companies.files'].delete_one({'_id': file._id})


documents found: 51496
68 --> 0993261068001_DocumentosGenerales_Certificado de Existencia Legal_2021-02-12_AB INBEV SOUTHERN INVESTMENTS LIMITED.pdf
68 --> 0991257721001_DocumentosGenerales_Oficio Transferencia Acciones_2010-03-11.pdf
68 --> 1792634318001_DocumentosGenerales_Formulario de Información de la Sociedad Extranjera_2021-12-30_SCHLUMBERGER PRODUCTION MANAGEMENT HOLDING B.V..pdf
68 --> 1790319857001_DocumentosGenerales_Oficio Transferencia Acciones_1989-01-20.pdf
68 --> 0990017514001_DocumentosGenerales_Oficio Nombramiento Administradores_1998-04-02_REYES PORTOCARRERO LUIS NORBERTO_DIRECTOR PRINCIPAL.pdf
68 --> 0990006687001_DocumentosGenerales_Oficio Nombramiento Administradores_2008-01-29_MITCHELL BEAVER NICHOLAS_GERENTE GENERAL.pdf
68 --> 1791251237001_DocumentosGenerales_Oficio Nombramiento Administradores_2008-09-16_AGUILAR VASQUEZ JUAN ANTONIO_PRESIDENTE EJECUTIVO.pdf
68 --> 0990293244001_DocumentosGenerales_Oficio Transferencia Acciones_1993-11-29.pdf
68 --> 09900235490

check if there are any duplicates 

In [57]:
pipeline = [
    {"$group": {"_id": "$filename", "count": {"$sum": 1}, "ids": {"$push": "$_id"}, "sizes": {"$push": "$length"}}},
    {"$match": {"count": {"$gt": 1}}}
]

duplicates = list(db['companies.files'].aggregate(pipeline))

for duplicate in duplicates:
    print(f"Filename: {duplicate['_id']}, Count: {duplicate['count']}")
    for file_id in duplicate['ids']:
        print(f"  - File ID: {file_id} - Size: {duplicate['sizes']}")
        # If teh size is the same then remove the firt one
        if len(set(duplicate['sizes'])) == 1:
            print(f"  - Removing file {file_id}")
            db['companies.files'].delete_one({'_id': file_id})
        # else delete the one that is the smallest
        else:
            # get the smallest file
            min_size = min(duplicate['sizes'])
            min_index = duplicate['sizes'].index(min_size)
            file_id = duplicate['ids'][min_index]
            print(f"  - Removing file {file_id}")
            db['companies.files'].delete_one({'_id': file_id})

Download every pdf and check if they are a valid pdf